# Setup and masking

In [12]:
import ee

# Trigger the authentication flow.
ee.Authenticate()

True

In [35]:
# Initialize the library.
ee.Initialize()
START_DATE = '2022-01-01'
END_DATE = '2022-06-01'
CLOUD_FILTER = 100 #Maximum image cloud cover percent allowed in image collection
CLD_PRB_THRESH = 35 #Cloud probability (%); values greater than are considered cloud
NIR_DRK_THRESH = 0.15
CLD_PRJ_DIST = 1
BUFFER = 50
# Define the range of days for mosaicking (15 days in this case)
DAY_RANGE = 15
LIST_FOLDER1 = ['bn_tb', 'dakya', 'dong_son_th', 'donghungThaiBinh', 'giao_thuy_nam_dinh', 
               'ha_trung_th', 'hai_hau_nam_dinh', 'haiduong', 'hoa_lu_ninh_binh', 'hue',
               'hungson', 'huylongan', 'kim_son_ninh_binh', 'my_loc_nam_dinh', 'nho_quan_ninh_binh',
               'ruonglongmy', 'thieu_hoa_th']
LIST_FOLDER = ['dakya', 'dong_son_th', 'haiduong', 'hue',
               'hungson', 'huylongan','ruonglongmy']

In [14]:
def get_s2_sr_cld_col(aoi, start_date, end_date):
    # Import and filter S2 SR.
    s2_sr_col = (ee.ImageCollection('COPERNICUS/S2_SR')
        .filterBounds(aoi)
        .filterDate(start_date, end_date)
        .filter(ee.Filter.lte('CLOUDY_PIXEL_PERCENTAGE', CLOUD_FILTER)))

    # Import and filter s2cloudless.
    s2_cloudless_col = (ee.ImageCollection('COPERNICUS/S2_CLOUD_PROBABILITY')
        .filterBounds(aoi)
        .filterDate(start_date, end_date))

    # Join the filtered s2cloudless collection to the SR collection by the 'system:index' property.
    return ee.ImageCollection(ee.Join.saveFirst('s2cloudless').apply(**{
        'primary': s2_sr_col,
        'secondary': s2_cloudless_col,
        'condition': ee.Filter.equals(**{
            'leftField': 'system:index',
            'rightField': 'system:index'
        })
    }))

In [15]:
def add_cloud_bands(img):
    # Get s2cloudless image, subset the probability band.
    cld_prb = ee.Image(img.get('s2cloudless')).select('probability')

    # Condition s2cloudless by the probability threshold value.
    is_cloud = cld_prb.gt(CLD_PRB_THRESH).rename('clouds')

    # Add the cloud probability layer and cloud mask as image bands.
    return img.addBands(ee.Image([cld_prb, is_cloud]))

In [16]:
def add_shadow_bands(img):
    # Identify water pixels from the SCL band.
    not_water = img.select('SCL').neq(6)

    # Identify dark NIR pixels that are not water (potential cloud shadow pixels).
    SR_BAND_SCALE = 1e4
    dark_pixels = img.select('B8').lt(NIR_DRK_THRESH*SR_BAND_SCALE).multiply(not_water).rename('dark_pixels')

    # Determine the direction to project cloud shadow from clouds (assumes UTM projection).
    shadow_azimuth = ee.Number(90).subtract(ee.Number(img.get('MEAN_SOLAR_AZIMUTH_ANGLE')));

    # Project shadows from clouds for the distance specified by the CLD_PRJ_DIST input.
    cld_proj = (img.select('clouds').directionalDistanceTransform(shadow_azimuth, CLD_PRJ_DIST*10)
        .reproject(**{'crs': img.select(0).projection(), 'scale': 100})
        .select('distance')
        .mask()
        .rename('cloud_transform'))

    # Identify the intersection of dark pixels with cloud shadow projection.
    shadows = cld_proj.multiply(dark_pixels).rename('shadows')

    # Add dark pixels, cloud projection, and identified shadows as image bands.
    return img.addBands(ee.Image([dark_pixels, cld_proj, shadows]))

In [17]:
def add_cld_shdw_mask(img):
    # Add cloud component bands.
    img_cloud = add_cloud_bands(img)

    # Add cloud shadow component bands.
    img_cloud_shadow = add_shadow_bands(img_cloud)

    # Combine cloud and shadow mask, set cloud and shadow as value 1, else 0.
    is_cld_shdw = img_cloud_shadow.select('clouds').add(img_cloud_shadow.select('shadows')).gt(0)

    # Remove small cloud-shadow patches and dilate remaining pixels by BUFFER input.
    # 20 m scale is for speed, and assumes clouds don't require 10 m precision.
    is_cld_shdw = (is_cld_shdw.focalMin(2).focalMax(BUFFER*2/20)
        .reproject(**{'crs': img.select([0]).projection(), 'scale': 20})
        .rename('cloudmask'))

    # Add the final cloud-shadow mask to the image.
    return img_cloud_shadow.addBands(is_cld_shdw)

In [18]:
def make_mask_cloud(image):    
    # Check if img is a valid Earth Engine image object
    if not isinstance(image, ee.Image):
        raise ValueError("The object is not an Earth Engine image.")
    
    # Subset layers and prepare them for display.
    shadows = image.select('shadows').Not()
    cloudmask = image.select('cloudmask').Not()

    img_mask = image.updateMask(cloudmask)
    img_mask = img_mask.updateMask(shadows)
    
    return img_mask

# NDVI data processing

## Functions and visualize

In [19]:
import json
import geemap
import numpy as np

def extract_tiff_image(image):
    etract_tiff = image.select(['B2', 'B3', 'B4', 'B8'])
    return etract_tiff

def calculate_ndvi(img):
    # Calculate NDVI: (NIR - Red) / (NIR + Red)
    ndvi = img.normalizedDifference(['B8', 'B4']).rename('NDVI')
    return ndvi

def mask_ndvi_with_clouds(ndvi, img_mask):
    # Apply the mask
    ndvi_masked = ndvi.updateMask(img_mask)
    return ndvi_masked

def get_ndvi_as_numpy(ndvi_masked, roi, scale):
    # Convert the masked NDVI image to a NumPy array
    ndvi_np = geemap.ee_to_numpy(ndvi_masked, region=roi, scale=scale)
    return ndvi_np

In [29]:
from scipy.signal import savgol_filter
from statsmodels.tsa.seasonal import STL
import pandas as pd
from scipy.interpolate import Akima1DInterpolator


def drop_ndvi_pixel(NDVI_image, range_time=10):
    drop_set = set()
    for month in range(0, NDVI_image.shape[0], range_time):
        series_img = NDVI_image[month:month + range_time, :, :]
        for x in range(NDVI_image.shape[1]):
            for y in range(NDVI_image.shape[2]):
                count = 0
                for i in range(series_img.shape[0]):
                    if np.isnan(series_img[i, x, y]):
                        count += 1
                if count == range_time:
                    drop_set.add((x, y))
                    continue
    return drop_set


def processing_ndvi_data(NDVI_image, drop_set, interpolation="linear", spatial=True, sg_filter=True):
    for x in range(NDVI_image.shape[1]):
        for y in range(NDVI_image.shape[2]):
            # if (x, y) in drop_set:
            #     continue

            if interpolation == "linear":
                filled_arr = NDVI_image[:, x, y]
                sr_filled_arr = pd.Series(filled_arr)
                sr_filled_arr.interpolate(method='linear', inplace=True)
                filled_arr = sr_filled_arr.to_numpy()
            elif interpolation == "stl":
                filled_arr = NDVI_image[:, x, y]
                sr_filled_arr = pd.Series(filled_arr)
                sr_filled_arr.interpolate(method='linear', inplace=True)
                #filled_arr = sr_filled_arr.to_numpy()
                stl = STL(sr_filled_arr, seasonal=53, period=53)  # Thêm tham số period
                result = stl.fit()
                seasonal = result.seasonal
                trend = result.trend
                residual = result.resid
                filled_arr = seasonal + trend + residual
            elif interpolation == 'akima':
                x = np.array(range(NDVI_image.shape[0]))
                y = NDVI_image[:, x, y]
                mask = ~np.isnan(y)  # Create a mask to filter out missing points
                x_valid = x[mask]
                y_valid = y[mask]
                # Create Akima interpolator object
                akima_interp = Akima1DInterpolator(x_valid, y_valid)
                # Interpolate missing values
                filled_arr = akima_interp(x)
        
            if sg_filter is True:
                # Applying Savitzky-Golay filter
                # Parameters: window_length and polyorder should be chosen based on your data
                window_length = 5  # The length of the filter window (must be odd)
                polyorder = 2      # The order of the polynomial to fit

                # Apply the SG filter
                filled_arr = savgol_filter(filled_arr, window_length=window_length, polyorder=polyorder)

            # Mean của các pixel xung quanh
            for month in range(NDVI_image.shape[0]):
                if np.isnan(NDVI_image[month, x, y]):
                    
                    neighbors = []
                    x_ = [-1, -1, -1, 0, 0, 1, 1, 1]
                    y_ = [-1, 0, 1, -1, 1, -1, 0, 1]
                    for k in range(len(x_)):
                        i = x + x_[k]
                        j = y + y_[k]
                    if (i < NDVI_image.shape[1] and i >= 0) and (j >= 0 and j < NDVI_image.shape[2]) and spatial is True:
                        if not np.isnan(NDVI_image[month, i, j]):
                            neighbors.append(NDVI_image[month, i , j])
                    if interpolation == "mean":
                        if month == 0:
                            NDVI_image[month, x, y] = np.mean([NDVI_image[month + 1, x, y], NDVI_image[month + 2, x, y]])
                        elif month == 52:
                            NDVI_image[month, x, y] = np.mean([NDVI_image[month - 1, x, y], NDVI_image[month - 2, x, y]])
                        elif month >= 1 and month < 52:
                            NDVI_image[month, x, y] = np.mean([NDVI_image[month - 1, x, y], NDVI_image[month + 1, x, y]])
                    elif interpolation in ["linear", "stl"] :
                        NDVI_image[month, x, y] = filled_arr[month]

                    if len (neighbors) > 0:
                        NDVI_image[month, x, y] = (NDVI_image[month, x, y] + np.mean(neighbors)) / 2

    return NDVI_image

In [43]:
from datetime import datetime, timedelta
from tqdm import tqdm
    
def compare_days(date1, date2):
    date1 = datetime.strptime(date1, "%Y%m%d")
    date2 = datetime.strptime(date2, "%Y%m%d")  
    
    # Calculate the difference in days
    difference = (date2 - date1).days

    # Check if the difference is 16 days
    if difference == 15:
        return True
    else:
        return False


# Function to create mosaics for each 15-day period
def create_mosaics(collection, start, end, AOI):
    # Filter collection between the start and end dates
    filtered = collection.filterDate(start, end)
    # Mosaic the filtered images
    mosaic = filtered.mosaic().clip(AOI)
    return mosaic.set('system:time_start', ee.Date(start).millis())


def get_npy_dataset(list_folder):
    dic = {}
    start_date = datetime.strptime(START_DATE, "%Y-%m-%d")
    arr_full = []
    for file_name in list_folder:
        area_arr = []
        with open(f"E:/EK_Intern/CropMonitoring/api/cfg/json/data_new/{file_name}.json") as f:
            json_file = json.load(f)
        
        AOI = ee.Geometry(json_file)
        collection = get_s2_sr_cld_col(AOI, START_DATE, END_DATE)
        dic[file_name] = collection
        collection_cld = collection.map(add_cld_shdw_mask).map(make_mask_cloud)
        f = collection_cld.toList(collection_cld.size().getInfo())
        #f2 = collection.toList(collection.size().getInfo())
        
        
        # Create a list to hold the mosaicked images
        mosaicked_images = []

        # Iterate over the date range and create mosaics for each 15-day window
        current_start = ee.Date(START_DATE) 
        # If END_DATE is a string or ee.Date, first compute the difference in days
        num_days = ee.Date(END_DATE).difference(current_start, 'day').round()

        # Now, advance by that number of days
        current_end = current_start.advance(num_days, 'day')


        while current_start.difference(END_DATE, 'day').getInfo() < 0:
            mosaic = create_mosaics(collection_cld, current_start.format('YYYY-MM-dd').getInfo(),
                                    current_end.format('YYYY-MM-dd').getInfo(), AOI)
            print(mosaic)
            mosaicked_images.append(mosaic)
            
            # Advance the window
            current_start = current_start.advance(DAY_RANGE, 'day')
            current_end = current_end.advance(DAY_RANGE, 'day')
        
        
        
        for i in tqdm(range(len(mosaicked_images)),desc=f"{file_name}: "):
            img = mosaicked_images[i]
            
            img = make_mask_cloud(img)

            # Compute NDVI
            ndvi = calculate_ndvi(img)  
            
            # Define region of interest and scale
            scale = 10  # Sentinel-2 resolution is 10m

            # Convert to NumPy array
            ndvi_np = geemap.ee_to_numpy(ndvi, region=AOI, scale=scale)

            # Check the shape of the masked array
            #img_date = datetime.strptime(img.getInfo()['properties']['system:index'][:8], "%Y%m%d")
            
            # if i == 0:
            #     start_date = img_date
            
            # if (img_date - start_date).days % 15 == 0:
            area_arr.append(ndvi_np)
        
        arr_full.append(area_arr)
    
    return arr_full, dic

In [44]:
arr_full, dic = get_npy_dataset(LIST_FOLDER[:1])

ee.Image({
  "functionInvocationValue": {
    "functionName": "Element.set",
    "arguments": {
      "key": {
        "constantValue": "system:time_start"
      },
      "object": {
        "functionInvocationValue": {
          "functionName": "Image.clip",
          "arguments": {
            "geometry": {
              "functionInvocationValue": {
                "functionName": "GeometryConstructors.Polygon",
                "arguments": {
                  "coordinates": {
                    "constantValue": [
                      [
                        [
                          108.295283,
                          14.010695
                        ],
                        [
                          108.294168,
                          14.008551
                        ],
                        [
                          108.292944,
                          14.006823
                        ],
                        [
                          108.29185,
         

KeyboardInterrupt: 

In [24]:
for i in arr_full[0]:
    #print(i, end=': ')
    print(np.squeeze(i, axis=2).shape)

2022-01-02 00:00:00: (165, 106)
2022-01-02 00:00:00: (165, 108)
2022-01-17 00:00:00: (165, 106)
2022-01-17 00:00:00: (165, 108)
2022-02-01 00:00:00: (165, 106)
2022-02-01 00:00:00: (165, 108)
2022-02-16 00:00:00: (165, 106)
2022-02-16 00:00:00: (165, 108)
2022-03-03 00:00:00: (165, 106)
2022-03-03 00:00:00: (165, 108)
2022-03-18 00:00:00: (165, 106)
2022-03-18 00:00:00: (165, 108)
2022-04-02 00:00:00: (165, 106)
2022-04-02 00:00:00: (165, 108)
2022-04-17 00:00:00: (165, 106)
2022-04-17 00:00:00: (165, 108)
2022-05-02 00:00:00: (165, 106)
2022-05-02 00:00:00: (165, 108)
2022-05-17 00:00:00: (165, 106)
2022-05-17 00:00:00: (165, 108)


In [17]:
import folium

def display_collected_image(area_index, index):
    with open(f"E:/EK_Intern/CropMonitoring/api/cfg/json/data_new/{LIST_FOLDER[area_index]}.json") as f:
        json_file = json.load(f)

    AOI = ee.Geometry(json_file)
    
    collection = dic[LIST_FOLDER[area_index]]
    collection_added = collection.map(add_cld_shdw_mask)
    collect_cloud_free = collection_added.map(make_mask_cloud)
    f = collect_cloud_free.toList(collect_cloud_free.size().getInfo())
    f2 = collection.toList(collection.size().getInfo())
    #img = ee.Image(f.get(index)).clip(AOI)
    #img = make_mask_cloud(img)
    img = ee.Image(f2.get(index)).clip(AOI)
    #print(img)
    
    center = AOI.centroid(10).coordinates().reverse().getInfo()
    m = folium.Map(location=center, zoom_start=24)
    
    # Add layers to the folium map.
    m.add_ee_layer(img,
                   {'bands': ['B4', 'B3', 'B2'], 'min': 0, 'max': 3000, 'gamma': 1.1},
                   'S2 image', True, 1, 9)
    
    # Add a layer control panel to the map.
    m.add_child(folium.LayerControl())

    # Display the map.
    display(m)

In [23]:
display_collected_image(0, 2)

In [ ]:
display_collected_image(0, -4)

In [ ]:
arr_full[0][]

In [313]:
for collection in dic.keys():
    print(collection, ":" ,dic[collection].size().getInfo())

dakya :  118
dong_son_th :  77
haiduong :  52
hue :  69
hungson :  61
huylongan :  69
ruonglongmy :  53


## Pipline

# Display

In [19]:
# Import the folium library.
import folium

# Define a method for displaying Earth Engine image tiles to a folium map.
def add_ee_layer(self, ee_image_object, vis_params, name, show=True, opacity=1, min_zoom=0):
    map_id_dict = ee.Image(ee_image_object).getMapId(vis_params)
    folium.raster_layers.TileLayer(
        tiles=map_id_dict['tile_fetcher'].url_format,
        attr='Map Data &copy; <a href="https://earthengine.google.com/">Google Earth Engine</a>',
        name=name,
        show=show,
        opacity=opacity,
        min_zoom=min_zoom,
        overlay=True,
        control=True
        ).add_to(self)

# Add the Earth Engine layer method to folium.
folium.Map.add_ee_layer = add_ee_layer

In [20]:
def display_cloud_layers(col, index, AOI):
    # Mosaic the image collection.
    f = col.toList(col.size().getInfo())
    img = ee.Image(f.get(index)).clip(AOI)
    

    center = AOI.centroid(10).coordinates().reverse().getInfo()
    m = folium.Map(location=center, zoom_start=30)
    collection = collection.map(add_cld_shdw_mask)
    collect_cloud_free = collection.map(make_mask_cloud)
    f = collect_cloud_free.toList(collect_cloud_free.size().getInfo())

    
    # Add layers to the folium map.
    m.add_ee_layer(img,
                   {'bands': ['B4', 'B3', 'B2'], 'min': 0, 'max': 2500, 'gamma': 1.1},
                   'S2 image', True, 1, 9)
    # m.add_ee_layer(probability,
    #                {'min': 0, 'max': 100},
    #                'probability (cloud)', False, 1, 9)
    # m.add_ee_layer(clouds,
    #                {'palette': 'e056fd'},
    #                'clouds', False, 1, 9)
    # m.add_ee_layer(cloud_transform,
    #                {'min': 0, 'max': 1, 'palette': ['white', 'black']},
    #                'cloud_transform', False, 1, 9)
    # m.add_ee_layer(dark_pixels,
    #                {'palette': 'orange'},
    #                'dark_pixels', False, 1, 9)
    # m.add_ee_layer(shadows, {'palette': 'yellow'},
    #                'shadows', False, 1, 9)
    # m.add_ee_layer(cloudmask, {'palette': 'orange'},
    #                'cloudmask', True, 0.5, 9)
    
    m.add_ee_layer(img_mask,
                   {'bands': ['B4', 'B3', 'B2'], 'min': 0, 'max': 2500, 'gamma': 1.1},
                   'S2 image mask cloud', True, 1, 9)
    # Add a layer control panel to the map.
    m.add_child(folium.LayerControl())

    # Display the map.
    display(m)

In [ ]:
with open(f"E:/EK_Intern/CropMonitoring/api/cfg/json/data_new/{LIST_FOLDER[1]}.json") as f:
    json_file = json.load(f)

AOI = ee.Geometry(json_file)

s2_sr_cld_col_eval = get_s2_sr_cld_col(AOI, START_DATE, END_DATE)

s2_sr_cld_col_eval_disp = s2_sr_cld_col_eval.map(add_cld_shdw_mask)

display_cloud_layers(s2_sr_cld_col_eval_disp, -1, AOI)